In [ ]:
%load_ext cython

In [ ]:
import sys
import Cython
print("Python %d.%d.%d %s %s" % sys.version_info)
print("Cython %s" % Cython.__version__)

# Static type declarations and Coercion

In [ ]:
%%cython -a

def add_one(x):
    return x + 1

def add_cint(x, int y):
    return x + y

cdef int A = 5

def add_cints(int x):
    return x + A

In [ ]:
add_one(5)

In [ ]:
add_cint(2, 4)

In [ ]:
add_cints(3)

# Functions

In [ ]:
%%cython

def pyfunc(x):
    return x + 1

def cyfunc(int x):
    return x + 1

cdef int cfunc(int x):
    return x + 1

cpdef cypyfunc(int x):
    y = cfunc(x + 1)
    return y * 2

In [ ]:
pyfunc(2)

In [ ]:
cyfunc(2)

In [ ]:
#cfunc(2)

In [ ]:
cypyfunc(2)

# Function "JIT compiling"

In [ ]:
# NOTE: Python code!

import cython

@cython.compile
def calc(a, b):
    for x in range(a):
        b += x
    return b
    

In [ ]:
calc(10, 20)

In [ ]:
type(calc)

# Calling C functions

In [ ]:
%%cython -a
# libc math functions
from libc cimport math

print( math.sin(math.M_PI / 2) )


In [ ]:
%%cython
# dynamic C memory allocation
from libc.stdlib cimport malloc, free

cdef int* cmem = <int*>malloc(22 * sizeof(int))
if not cmem:
    raise MemoryError()
free(cmem)


In [ ]:
%%cython
# dynamic CPython heap memory allocation
from cpython.mem cimport PyMem_Malloc, PyMem_Free

cdef int* pymem = <int*>PyMem_Malloc(22 * sizeof(int))
if not pymem:
    raise MemoryError()
    
try:
    pymem[:] = [1,2,3]
    print( pymem[0] + pymem[2] )
finally:
    PyMem_Free(pymem)


# Auto-wrapping C functions to Python

In [ ]:
%%cython -a
from libc cimport math, stdlib
py_sin = math.sin
py_atoi = stdlib.atoi

In [ ]:
py_sin(1/2)

In [ ]:
py_atoi(b'123')

# External libraries

In [ ]:
%%cython
# distutils: include_dirs=/usr/include/luajit-2.0
# distutils: libraries=luajit-5.1

## distutils: include_dirs=/usr/include/lua5.1
## distutils: libraries=lua5.1

cdef extern from "lua.h":
    ctypedef struct lua_State
    lua_State *luaL_newstate ()
    void lua_close (lua_State *L)
    int luaL_loadbuffer (lua_State *L, char *buff, size_t sz, char *name)
    void lua_settop (lua_State *L, int idx)
    int lua_gettop (lua_State *L)
    int lua_pcall (lua_State *L, int nargs, int nresults, int errfunc)
    int lua_type (lua_State *L, int idx)
    float lua_tonumber (lua_State *L, int idx)
    enum:
        LUA_TNUMBER
        LUA_MULTRET


def run_lua(code):
    cdef int result_status
    cdef float result

    if isinstance(code, unicode):
        code = code.encode('utf8')
    elif not isinstance(code, bytes):
        raise ValueError("code must be a string")

    # init Lua runtime
    L = luaL_newstate()
    if not L:
        raise MemoryError()

    try:
        # compile Lua code
        if luaL_loadbuffer(L, code, len(code), '<python>'):
            raise SyntaxError()

        # execute code
        if lua_pcall(L, 0, LUA_MULTRET, 0):
            raise RuntimeError()

        # convert return value (Lua number == float)
        assert lua_type(L, 1) == LUA_TNUMBER, "not a numeric return value"
        return lua_tonumber(L, 1)
    finally:
        lua_settop(L, 0)
        lua_close(L)


In [ ]:
code = '''
function fib(i)
    if i > 2 then
        return fib(i-1) + fib(i-2)
    else
        return 1
    end
end
'''

run_lua(code + "return fib(10)")

In [ ]:
%%timeit bench = code + "return fib(24)"

run_lua(bench)

In [ ]:
# distutils: include_dirs=/usr/include/luajit-2.0
# distutils: libraries=luajit-5.1


# C arrays

In [ ]:
%%cython -a
def carrays():
    cdef int[10] a, b

    a[:5] = [1,2,3,4,5]    # slice assignment
    b = a                  # copy by value
    b[5:] = [6,7,8,9,10]

    for i in b[:3]:        # for-loop iteration
        print(i+1)

    return b

In [ ]:
carrays()

# C++

In [ ]:
%%cython -a
# distutils: language=c++

from libcpp.vector cimport vector

def use_cpp_vector(*values):
    cdef vector[int] v = values

    if values:
        assert values[0] == v[0]

    # "validate" the copy above in N^2 time :)
    for c_value in v:
        assert c_value in values

    process_in_ext_cpp_func(v)

    return v


cdef void process_in_ext_cpp_func(vector[int] &v):
    ...


In [ ]:
use_cpp_vector(1, 4, 77)